In [ ]:
import boto3
session = boto3.Session(profile_name='slscode')
s3 = session.client('s3')

In [ ]:
s3.list_buckets()

In [ ]:
s3.list_objects_v2(Bucket='crop-catalog-assets')

In [ ]:
template_body = s3.get_object(Bucket='crop-catalog-assets', Key='templates/prod-7qedu6ehkucdi/template-22.json')
template_body

In [ ]:
import json
parsed_template = json.load(template_body['Body'])

In [ ]:
print(type(parsed_template))
parsed_template

In [ ]:
resp = s3.put_object(
    Bucket='ryansb-ansible-scratch',
    Key='test.json',
    ACL='public-read',
    ContentType='application/json',
    StorageClass='REDUCED_REDUNDANCY',
    Body=json.dumps(parsed_template)
)
resp

In [ ]:
import gzip

with gzip.open('/tmp/tpl.json.gz', mode='wb', compresslevel=9) as compress:
    s3.download_fileobj(
        Bucket='crop-catalog-assets',
        Key='templates/prod-7qedu6ehkucdi/template-22.json',
        Fileobj=compress)

In [ ]:
resp = s3.put_object(
    Bucket='ryansb-ansible-scratch',
    Key='test.json.gz',
    ACL='public-read',
    ContentType='application/json',
    ContentEncoding='gzip',
    StorageClass='REDUCED_REDUNDANCY',
    Body=open('/tmp/tpl.json.gz', 'rb')
)
resp

In [ ]:
with open('/tmp/tpl.json.gz', 'rb') as fh: print(len(fh.read()))

In [ ]:
s3.head_object(Bucket='ryansb-ansible-scratch', Key='test.json')

In [ ]:
s3.head_object(Bucket='ryansb-ansible-scratch', Key='test.json.gz')

# Now with Resources!

In [ ]:
bukkit = session.resource('s3').Bucket('ryansb-ansible-scratch')

In [ ]:
for obj in bukkit.objects.all():
    print(obj.key, obj.e_tag, obj.size)
    if obj.size > 2**30: obj.delete()